<a href="https://colab.research.google.com/github/AnnJer/Practice_in_Data_Preprocessing/blob/master/nlp_routine3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
import pandas as pd

from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction import text

from nltk.stem import WordNetLemmatizer
import nltk.stem
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize

from stop_words import get_stop_words
import re
import numpy as np
import eli5
import lime
import h5py
import splitter
import time

In [0]:
data1 = pd.read_csv('commits.csv')
data2 = pd.read_csv('issues.csv')

data= pd.merge(data1, data2, on='key', how='inner')

X = data.drop(data.columns.difference(['message_encoding']), 1)
y = data.drop(data.columns.difference(['severity']), 1)

# X_train,  X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42 )

### Cleaning the text, remove unnecessary words and signs

In [0]:
pattern1 = re.compile(r'\[.+?\]')
X['message_encoding'] = X['message_encoding'].apply(lambda text: pattern1.subn('', text)[0])

X['message_encoding'] = X['message_encoding'].replace('\d+', 'NUM', regex=True)

pattern2 = re.compile(r'Author.+',  re.S)
X['message_encoding'] = X['message_encoding'].apply(lambda text: pattern2.subn('', text)[0])

In [0]:
my_stop_words = text.ENGLISH_STOP_WORDS.union(list(get_stop_words('en'))) 

In [0]:
class TokenizingCountVect(object):
    
    """
    split the document into sentences and tokenize each sentence
    """
    def __init__(self):
        self.count_vec = CountVectorizer(stop_words=my_stop_words,
#                                          token_pattern=r'\b[^\d\W]+\b', 
                                         analyzer='word', 
                                         ngram_range=(1, 1), 
                                         max_df=1.0, 
                                         min_df=1, 
                                         max_features=None)
        
    def fit_transform(self, data):
        bag_of_words = self.count_vec.fit_transform(data)   
        print('number of words ', len(self.count_vec.get_feature_names()))
        print(self.count_vec.get_feature_names())

        
start_time = time.time()        
TokenizingCountVect().fit_transform(X.message_encoding)
print("--- %s seconds ---" % (time.time() - start_time))


/home/ann/anaconda3/lib/python3.7/site-packages/sklearn/feature_extraction/text.py:300: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['aren', 'couldn', 'didn', 'doesn', 'don', 'hadn', 'hasn', 'haven', 'isn', 'let', 'll', 'mustn', 'shan', 'shouldn', 've', 'wasn', 'weren', 'won', 'wouldn'] not in stop_words.
  'stop_words.' % sorted(inconsistent))


number of words  21182
['__', '___', '____', '_____', '__all__', '__alpha', '__app__', '__barrier', '__builtin__', '__call__', '__consumer_offsets', '__contains__', '__create', '__datatype__', '__eager__', '__eq__', '__fields__', '__getattr__', '__getitem__', '__getslice__', '__gettitem__', '__hash__', '__hive', '__hive_default_partition__', '__init__', '__lazy__', '__len__', '__main__', '__module__', '__name__', '__notes__', '__repl__', '__repr__', '__run', '__shared', '__spark_conf__', '__spark_conf__num', '__spark_libs__num', '__str__', '__summary', '__this__', '__version__', '_acceptable_types', '_aggordering', '_all_', '_also', '_also_', '_are_', '_at', '_avg', '_batch', '_batched', '_before_', '_buffer_decode', '_build', '_cached_cls', '_cancelled', '_case', '_changes', '_checktype', '_childclusters', '_childnodes', '_cnum', '_codegened_', '_col', '_collection_functions', '_common', '_compare_params', '_compile_', '_conf', '_config', '_copy_n', '_copy_new_parent', '_corrupt_recor

In [0]:
class  TokenizingTFIDF(object):
    """
    split words wth using tf-idf
    """
    def __init__(self):
        self.tfidf = TfidfVectorizer(stop_words=my_stop_words, 
                                     ngram_range=(2, 2), 
                                     sublinear_tf= True ,
                                     norm='l2')
        pass
    
    def fit_transform(self, data):
        tfidf = self.tfidf.fit_transform(data)
        print(len(self.tfidf.get_feature_names()))
        
TokenizingTFIDF().fit_transform(X.message_encoding)

222294


In [0]:
from gensim.models import Word2Vec

In [0]:

stemmer = nltk.stem.SnowballStemmer('english')

# class StemmedCountVectorizer(CountVectorizer):
#     def build_analyzer(self):
#         analyzer = super(StemmedCountVectorizer, self).build_analyzer()
#         return lambda doc: (stemmer.stem(w) for w in analyzer(doc))


my_stop_words = text.ENGLISH_STOP_WORDS.union(list(get_stop_words('en')))        
count_vec = CountVectorizer(stop_words=my_stop_words,
                            token_pattern=r'\b[^\d\W]+\b', 
                            analyzer='word', 
                            ngram_range=(1, 1), 
                            max_df=1.0, 
                            min_df=1, 
                            max_features=None)

bag_of_words = count_vec.fit_transform(X.message_encoding)

print(count_vec.get_feature_names())

['_', '__', '___', '____', '_____', '__all__', '__alpha', '__app__', '__barrier', '__builtin__', '__call__', '__consumer_offsets', '__contains__', '__create', '__datatype__', '__eager__', '__eq__', '__fields__', '__getattr__', '__getitem__', '__getslice__', '__gettitem__', '__hash__', '__hive', '__hive_default_partition__', '__init__', '__lazy__', '__len__', '__main__', '__module__', '__name__', '__notes__', '__repl__', '__repr__', '__run', '__shared', '__spark_conf__', '__spark_conf__num', '__spark_libs__num', '__str__', '__summary', '__this__', '__version__', '_acceptable_types', '_aggordering', '_all_', '_also', '_also_', '_are_', '_at', '_avg', '_batch', '_batched', '_before_', '_buffer_decode', '_build', '_cached_cls', '_cancelled', '_case', '_changes', '_checktype', '_childclusters', '_childnodes', '_cnum', '_codegened_', '_col', '_collection_functions', '_common', '_compare_params', '_compile_', '_conf', '_config', '_copy_n', '_copy_new_parent', '_corrupt_record', '_dataset', '_

In [0]:
lemmat = WordNetLemmatizer()
prepeared_text = lemmat.lemmatize(count_vec.get_feature_names(), pos = 'v')


print("Every feature:\n{}".format(len(count_vec.get_feature_names())))


<11475x21209 sparse matrix of type '<class 'numpy.int64'>'
	with 353605 stored elements in Compressed Sparse Row format>

In [0]:
tf_idf = TfidfVectorizer(smooth_idf=False,
                         sublinear_tf=False, 
                         norm=None,
                         analyzer='word',
                         stop_words=my_stop_words, 
                         max_features=30000)

txt_fitted = tf_idf.fit(X.message_encoding)
txt_transformed = txt_fitted.transform(X.message_encoding)

# print(dict(zip(txt_fitted.get_feature_names(), tf_idf.idf_)))

In [0]:
feature_names = np.array(tf_idf.get_feature_names())
sorted_by_idf = np.argsort(tf_idf.idf_)
print("Features with lowest idf:\n{}".format(
       feature_names[sorted_by_idf[:3]]))
print("\nFeatures with highest idf:\n{}".format(
       feature_names[sorted_by_idf[-3:]]))

In [0]:
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet

text = 'What can I say about this place. The staff of these restaurants is nice and the eggplant is not bad'

class Splitter(object):
    """
    split the document into sentences and tokenize each sentence
    """
    def __init__(self):
        self.splitter = nltk.data.load('tokenizers/punkt/english.pickle')
        self.tokenizer = nltk.tokenize.TreebankWordTokenizer()

    def split(self,text):
        """
        out : ['What', 'can', 'I', 'say', 'about', 'this', 'place', '.']
        """
        # split into single sentence
        sentences = self.splitter.tokenize(text)
        # tokenization in each sentences
        tokens = [self.tokenizer.tokenize(sent) for sent in sentences]
        return tokens


class LemmatizationWithPOSTagger(object):
    def __init__(self):
        pass
    def get_wordnet_pos(self,treebank_tag):
        """
        return WORDNET POS compliance to WORDENT lemmatization (a,n,r,v) 
        """
        if treebank_tag.startswith('J'):
            return wordnet.ADJ
        elif treebank_tag.startswith('V'):
            return wordnet.VERB
        elif treebank_tag.startswith('N'):
            return wordnet.NOUN
        elif treebank_tag.startswith('R'):
            return wordnet.ADV
        else:
            # As default pos in lemmatization is Noun
            return wordnet.NOUN

    def pos_tag(self,tokens):
        # find the pos tagginf for each tokens [('What', 'WP'), ('can', 'MD'), ('I', 'PRP') ....
        pos_tokens = [nltk.pos_tag(token) for token in tokens]

        # lemmatization using pos tagg   
        # convert into feature set of [('What', 'What', ['WP']), ('can', 'can', ['MD']), ... ie [original WORD, Lemmatized word, POS tag]
        pos_tokens = [ [lemmatizer.lemmatize(word,self.get_wordnet_pos(pos_tag)) for (word,pos_tag) in pos] for pos in pos_tokens]
        return pos_tokens

lemmatizer = WordNetLemmatizer()
splitter = Splitter()
lemmatization_using_pos_tagger = LemmatizationWithPOSTagger()

#step 1 split document into sentence followed by tokenization
tokens = splitter.split(text)

#step 2 lemmatization using pos tagger 
lemma_pos_token = lemmatization_using_pos_tagger.pos_tag(tokens)
print(lemma_pos_token)


In [0]:
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer 
ps = PorterStemmer()

start_time = time.time()

for words in X.message_encoding:
    words = word_tokenize(words)
    print(words)
#     for w in words:
#         print(ps.stem(w))
print("--- %s seconds ---" % (time.time() - start_time))
# X.message_encoding

['Removal', 'of', 'Hive', 'Built-in', 'Hash', 'Functions', 'and', 'TestHiveFunctionRegistry', '#', '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', 'Currently', ',', 'the', 'Hive', 'built-in', '`', 'hash', '`', 'function', 'is', 'not', 'being', 'used', 'in', 'Spark', 'since', 'Spark', 'NUM.NUM', '.', 'The', 'public', 'interface', 'does', 'not', 'allow', 'users', 'to', 'unregister', 'the', 'Spark', 'built-in', 'functions', '.', 'Thus', ',', 'users', 'will', 'never', 'use', 'Hive', "'s", 'built-in', '`', 'hash', '`', 'function', '.', 'The', 'only', 'exception', 'here', 'is', '`', 'TestHiveFunctionRegistry', '`', ',', 'which', 'allows', 'users', 'to', 'unregister', 'the', 'built-in', 'functions', '.', 'Thus', ',', 'we', 'can', 'load', 'Hive', "'s", 'hash', 'function', 'in', 'the', 'test', 'cases', '.', 'If', 'we', 'disable', 'it', ',', 'NUM+', 'test', 'cases', 'will', 'fail', 'because', 'the', 'results', 'are', 'different', 'from', 'the', 'Hive', 'gol

['Add', 'examples', '(', 'extend', ')', 'in', 'each', 'expression', 'and', 'improve', 'documentation', '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', 'This', 'PR', 'proposes', 'to', 'change', 'the', 'documentation', 'for', 'functions', '.', 'Please', 'refer', 'the', 'discussion', 'from', 'https', ':', '//github.com/apache/spark/pull/NUM', 'The', 'changes', 'include', '-', 'Re-indent', 'the', 'documentation', '-', 'Add', 'examples/arguments', 'in', '`', 'extended', '`', 'where', 'the', 'arguments', 'are', 'multiple', 'or', 'specific', 'format', '(', 'e.g', '.', 'xml/', 'json', ')', '.', 'For', 'examples', ',', 'the', 'documentation', 'was', 'updated', 'as', 'below', ':', '#', '#', '#', 'Functions', 'with', 'single', 'line', 'usage', '**Before**', '-', '`', 'pow', '`', '``', '`', 'sql', 'Usage', ':', 'pow', '(', 'xNUM', ',', 'xNUM', ')', '-', 'Raise', 'xNUM', 'to', 'the', 'power', 'of', 'xNUM', '.', 'Extended', 'Usage', ':', '>', 'SELECT', 'pow', '

['store', 'partition', 'spec', 'in', 'metastore', 'for', 'data', 'source', 'table', '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', 'We', 'should', 'follow', 'hive', 'table', 'and', 'also', 'store', 'partition', 'spec', 'in', 'metastore', 'for', 'data', 'source', 'table', '.', 'This', 'brings', 'NUM', 'benefits', ':', 'NUM', '.', 'It', "'s", 'more', 'flexible', 'to', 'manage', 'the', 'table', 'data', 'files', ',', 'as', 'users', 'can', 'use', '`', 'ADD', 'PARTITION', '`', ',', '`', 'DROP', 'PARTITION', '`', 'and', '`', 'RENAME', 'PARTITION', '`', 'NUM', '.', 'We', 'do', "n't", 'need', 'to', 'cache', 'all', 'file', 'status', 'for', 'data', 'source', 'table', 'anymore', '.', '#', '#', 'How', 'was', 'this', 'patch', 'tested', '?', 'existing', 'tests', '.']
['Fix', 'test', '``', 'StreamExecution', 'metadata', 'garbage', 'collection', "''", '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', 'A', 'follow', 'up', 'PR',

['Introduce', 'performant', 'and', 'memory', 'efficient', 'APIs', 'to', 'create', 'ArrayBasedMapData', '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', 'Jira', ':', 'https', ':', '//issues.apache.org/jira/browse/SPARK-NUM', 'In', 'HiveInspectors', ',', 'I', 'saw', 'that', 'converting', 'Java', 'map', 'to', 'Spark', "'s", '`', 'ArrayBasedMapData', '`', 'spent', 'quite', 'sometime', 'in', 'buffer', 'copying', ':', 'https', ':', '//github.com/apache/spark/blob/master/sql/hive/src/main/scala/org/apache/spark/sql/hive/HiveInspectors.scala', '#', 'LNUM', 'The', 'reason', 'being', '`', 'map.toSeq', '`', 'allocates', 'a', 'new', 'buffer', 'and', 'copies', 'the', 'map', 'entries', 'to', 'it', ':', 'https', ':', '//github.com/scala/scala/blob/NUM.NUM.x/src/library/scala/collection/MapLike.scala', '#', 'LNUM', 'This', 'copy', 'is', 'not', 'needed', 'as', 'we', 'get', 'rid', 'of', 'it', 'once', 'we', 'extract', 'the', 'key', 'and', 'value', 'arrays', '.', 'Her

['MetastoreRelation', 'should', 'talk', 'to', 'external', 'catalog', 'instead', 'of', 'hive', 'client', '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', '`', 'HiveExternalCatalog', '`', 'should', 'be', 'the', 'only', 'interface', 'to', 'talk', 'to', 'the', 'hive', 'metastore', '.', 'In', '`', 'MetastoreRelation', '`', 'we', 'can', 'just', 'use', '`', 'ExternalCatalog', '`', 'instead', 'of', '`', 'HiveClient', '`', 'to', 'interact', 'with', 'hive', 'metastore', ',', 'and', 'add', 'missing', 'API', 'in', '`', 'ExternalCatalog', '`', '.', '#', '#', 'How', 'was', 'this', 'patch', 'tested', '?', 'existing', 'tests', '.']
['Break', 'fileSourceInterfaces.scala', 'into', 'multiple', 'pieces', '#', '#', 'What', 'changes', 'were', 'proposed', 'in', 'this', 'pull', 'request', '?', 'This', 'patch', 'does', 'a', 'few', 'changes', 'to', 'the', 'file', 'structure', 'of', 'data', 'sources', ':', '-', 'Break', 'fileSourceInterfaces.scala', 'into', 'multiple', 'piec

...

['Fix', 'the', 'bug', 'that', 'streaming', "'s", 'receiver', 'may', 'fall', 'into', 'a', 'dead', 'loop']
['Fix', 'the', 'bug', 'that', 'streaming', "'s", 'receiver', 'may', 'fall', 'into', 'a', 'dead', 'loop']
['SparkFlumeEvent', 'with', 'body', 'bigger', 'than', 'NUM', 'bytes', 'are', 'not', 're', '...', 'flume', 'event', 'sent', 'to', 'Spark', 'will', 'fail', 'if', 'the', 'body', 'is', 'too', 'large', 'and', 'numHeaders', 'is', 'greater', 'than', 'zero']
['SPARK-NUM', ':', 'Fix', 'potential', 'resource', 'leaks', 'JIRA', ':', 'https', ':', '//issues.apache.org/jira/browse/SPARK-NUM', 'Move', 'the', '``', 'close', "''", 'statements', 'into', 'a', '``', 'finally', "''", 'block', '.']
['Change', 'recursive', 'visiting', 'on', 'RDD', 'dependencies', 'to', 'iterative', 'approach', 'When', 'performing', 'some', 'transformations', 'on', 'RDDs', 'after', 'many', 'iterations', ',', 'the', 'dependencies', 'of', 'RDDs', 'could', 'be', 'very', 'long', '.', 'It', 'can', 'easily', 'cause', 'StackO

['Remove', '<', 'master', '>', 'from', 'Python', 'examples', 'A', 'recent', 'PR', '(', '#', 'NUM', ')', 'fixed', 'this', 'for', 'all', 'Scala', '/', 'Java', 'examples', '.', 'We', 'need', 'to', 'do', 'it', 'for', 'python', 'too', '.', 'Note', 'that', 'this', 'blocks', 'on', '#', 'NUM', ',', 'which', 'makes', '`', 'bin/pyspark', '`', 'go', 'through', 'Spark', 'submit', '.', 'With', 'only', 'the', 'changes', 'in', 'this', 'PR', ',', 'the', 'only', 'way', 'to', 'run', 'these', 'examples', 'is', 'through', 'Spark', 'submit', '.', 'Once', '#', 'NUM', 'goes', 'in', ',', 'you', 'can', 'use', '`', 'bin/pyspark', '`', 'to', 'run', 'them', 'too', '.', 'For', 'example', ',', '``', '`', 'bin/pyspark', 'examples/src/main/python/pi.py', 'NUM', '--', 'master', 'local-cluster', '``', '`']
['Route', 'bin/pyspark', 'through', 'Spark', 'submit', '**Problem', '.', '**', 'For', '`', 'bin/pyspark', '`', ',', 'there', 'is', 'currently', 'no', 'other', 'way', 'to', 'specify', 'Spark', 'configuration', 'proper

['SPARK-NUM', ':', 'Use', 'SPARK_HIVE', 'to', 'determine', 'if', 'we', 'include', 'Hive', 'in', 'packaging', 'Previously', ',', 'we', 'based', 'our', 'decision', 'regarding', 'including', 'datanucleus', 'jars', 'based', 'on', 'the', 'existence', 'of', 'a', 'spark-hive-assembly', 'jar', ',', 'which', 'was', 'incidentally', 'built', 'whenever', '``', 'sbt', 'assembly', "''", 'is', 'run', '.', 'This', 'means', 'that', 'a', 'typical', 'and', 'previously', 'supported', 'pathway', 'would', 'start', 'using', 'hive', 'jars', '.', 'This', 'patch', 'has', 'the', 'following', 'features/bug', 'fixes', ':', '-', 'Use', 'of', 'SPARK_HIVE', '(', 'default', 'false', ')', 'to', 'determine', 'if', 'we', 'should', 'include', 'Hive', 'in', 'the', 'assembly', 'jar', '.', '-', 'Analagous', 'feature', 'in', 'Maven', 'with', '-Phive', '(', 'previously', ',', 'there', 'was', 'no', 'support', 'for', 'adding', 'Hive', 'to', 'any', 'of', 'our', 'jars', 'produced', 'by', 'Maven', ')', '-', 'assemble-deps', 'fixed'

['Merge', 'pull', 'request', '#', 'NUM', 'from', 'JoshRosen/spark-NUM', 'Do', 'not', 'launch', 'JavaGateways', 'on', 'workers', '(', 'SPARK-NUM', ')', '.']
['Do', 'not', 'launch', 'JavaGateways', 'on', 'workers', '(', 'SPARK-NUM', ')', '.', 'The', 'problem', 'was', 'that', 'the', 'gateway', 'was', 'being', 'initialized', 'whenever', 'the', 'pyspark.context', 'module', 'was', 'loaded', '.', 'The', 'fix', 'uses', 'lazy', 'initialization', 'that', 'occurs', 'only', 'when', 'SparkContext', 'instances', 'are', 'actually', 'constructed', '.', 'I', 'also', 'made', 'the', 'gateway', 'and', 'jvm', 'variables', 'private', '.', 'This', 'change', 'results', 'in', '~NUM-NUMx', 'performance', 'improvement', 'when', 'running', 'the', 'PySpark', 'unit', 'tests', '.']
['Merge', 'pull', 'request', '#', 'NUM', 'from', 'pwendell/python-exceptions', 'SPARK-NUM', ':', 'Capture', 'and', 're-throw', 'Python', 'exceptions']
['SPARK-NUM', ':', 'Capture', 'and', 're-throw', 'Python', 'exceptions', 'This', 'patch

['Merge', 'pull', 'request', '#', 'NUM', 'from', 'mateiz/confNUM', 'SPARK-NUM', '.', 'Migrate', 'configuration', 'to', 'a', 'SparkConf', 'class', 'This', 'is', 'still', 'a', 'work', 'in', 'progress', 'based', 'on', 'Prashant', 'and', 'Evan', "'s", 'code', '.', 'So', 'far', 'I', "'ve", 'done', 'the', 'following', ':', '-', 'Got', 'rid', 'of', 'global', 'SparkContext.globalConf', '-', 'Passed', 'SparkConf', 'to', 'serializers', 'and', 'compression', 'codecs', '-', 'Made', 'SparkConf', 'public', 'instead', 'of', 'private', '-', 'Improved', 'API', 'of', 'SparkContext', 'and', 'SparkConf', '-', 'Switched', 'executor', 'environment', 'vars', 'to', 'be', 'passed', 'through', 'SparkConf', '-', 'Fixed', 'some', 'places', 'that', 'were', 'still', 'using', 'system', 'properties', '-', 'Fixed', 'some', 'tests', ',', 'though', 'others', 'are', 'still', 'failing', 'This', 'still', 'fails', 'several', 'tests', 'in', 'core', ',', 'repl', 'and', 'streaming', ',', 'likely', 'due', 'to', 'properties', 'n